In this exercise you will download the audio of a youtube video, convert it to the WAV format, and then use the Google Cloud API to transcribe its content.

The lines below import some libraries that make this quite simple. Summerized they are:

 * **pafy**, a library to download youtube video and audio.
 * **pydub**, a library to convert audio, for example from mp3 to wav.
 * **google api**, contains a lot of stuff, in particular audio transcription using the speech API. This is done on a Google server, you send it audio and get a transcription back. This way Google can improve their machine learning algorithms and serve this to you.


This exercise uses reasonably complicated syntax and things you have not learned properly. Do not worry too much about that, try to understand what is happening. We only ask you to insert small and simple pieces of code.

Select the 'cell' below and press CTRL+ENTER or SHIFT+ENTER to run the code inside it.

In [ ]:
# !pip install pafy pydub youtube-dl google-cloud google-cloud-speech google-api-python-client

# import sys
# !conda install --yes --prefix {sys.prefix} -c conda-forge ffmpeg 

In [ ]:
import os
os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = 'credentials.json'
os.environ['PATH'] += ';' + os.path.join(os.path.abspath(os.curdir), 'bin')

import io
import pafy
from pydub import AudioSegment

from google.cloud import speech
from google.cloud.speech import enums
from google.cloud.speech import types

from googleapiclient import discovery

First use `pafy` to get some information of a video.

**Exercise:** What are the types of url, video and video.length? You can use function `type( ... )` to find out.

In [ ]:
# YOUR CODE HERE, ~ 3 lines
None
None
None

Run the cell.

In [ ]:
url = 'https://www.youtube.com/watch?v=yY-P3D63Z18'

video = pafy.new(url)

print("Url:", url)
print("Title:", video.title)
print("Author:", video.author)
print("Description:", video.description)
print("Length:", video.length)

Now let's actually download the audio of the video and save it. The first line gets the best audio format from the existing ones (YouTube provides multiple formats and encodings of video and audio).

The second line downloads the file to `audio.webm`.

Run the cell.

In [ ]:
audio = video.getbestaudio()

# remove the file if it already exists
if os.path.exists(audio.filename):
    os.unlink(audio.filename)

filename = audio.download(filepath=audio.filename)
print("Filename:", filename)

Google's api works easier with a WAV file than with a WEBM file (even though webm is their own format). Moreover, the audio cannot be more than 60 seconds long. Longer audio need the so called `streaming api`, which is a bit harder to use.

Let's keep it simple. The recipe below is, line by line:

 * open the WEBM file
 * save it as WAV
 * show the audio
 
Run the cell.

In [ ]:
sound = AudioSegment.from_file(audio.filename)

sound.export("audio.wav", format="wav", bitrate="128k")

sound

The variable `sound` contains an `AudioSegment`, an object with `frame_count()` method and a `frame_rate` attribute. 

As you may know, sound is a wave. For computers to store such waves, an audio file is composed of many frames. Each frame specifies the amplitude of the wave at a specific time. `frame_count()` calculates how many frames there are in total, and `frame_rate` states how many frames should go in one second.

**Excercise:** Divide `frame_count()` by `frame_rate` to find out how many seconds are exactly in the audio file. Use both `/` and `//` for the devision, what is the difference?

In [ ]:
print("type(sound): ", type(sound))

# YOUR CODE HERE, ~ 2 lines, use both / and //
audio_length_s  = None      # Use /
audio_length_s_ = None      # Use //
# END OF YOUR CODE

print("audio_length_s: ", audio_length_s)
print("audio_length_s_: ", audio_length_s_)

Now that we have a WAV file, we use the tools google provide to load these files in a data type Google likes, and we also specify a configuration which states that we want English transcriptions. This improves the transcriptions quality, as now the system know that **Je t'adore** is less likely to occur as **Shut the door**.

The first two lines open the audio file and place its data in memory.

The third line converts the data to a format in which Google can handle.

The last line creates a configuration for the transcription task (in which the language is also specifyied).

Run the cell.

In [ ]:
with open('audio.wav', 'rb') as audio_file:
    content = audio_file.read()

audio = types.RecognitionAudio(content=content)
config = types.RecognitionConfig(language_code='en-US')

Let's start transcoding. The first line creates a client, which is sort of a telephone that does the communication with Google.

The second line does the hard work, or at least asks Google to do so.

Run the cell (**it will result in an error**).

Read the message, however cryptic it may seem. What does this error mean?

 * A) You need to pay for this Google service,
 * B) You need to make an appointment (rendezvous) with a service agent from Google
 * C) The audio was too long, and this API only accepts smaller files
 * D) Google speech does not support audio files in stereo
 * E) The transcription service was permanently terminated in 2016, Google now only offers web search and e-mail

In [ ]:
client = speech.SpeechClient()

response = client.recognize(config, audio)

An important part of programming is failing. No code was ever right the first time and most code isn't even right in the final version. `github.com` is a place to distribute software, but also register software bugs and manage solutions. Browse some of the issues there and you'll get the point (or not browse the site, and trust me on this).

This issue is with the file length, it's too large as Google only allows 60 seconds. So let's extract **the first 30 seconds** and try again.

To extract a time slice, the syntax is `[ <start_in_miliseconds> : <end_in_miliseconds> ]`. If you leave the start out, it starts from the beginning. If you leave the end out, it ends at the end. 

**Exercise:** Correct the error. For that, choose the correct line out of the 5 commented lines. 

All text after a hashtag (`#`) is commented, that is, <u>ignored by the computer</u>. This way you can disable code or add comments. You can uncomment a pieace of code by deleting the hashtag (`#`).

*TIP*: You can test each option by uncommenting one at a time.

In [ ]:
sound = AudioSegment.from_file(filename)

### Select one of these 5 options by removing the # and the space:
# sound = sound[:]
# sound = sound[1000:]
# sound = sound.get_sample_slice(0, 5*44000)
# sound = sound.split_to_mono()[0]
# sound = sound[103]


sound.export("audio.wav", format="wav", bitrate="128k")

sound

In [ ]:
with open('audio.wav', 'rb') as audio_file:
    content = audio_file.read()

audio = types.RecognitionAudio(content=content)
config = types.RecognitionConfig(language_code='en-US')

In [ ]:
client = speech.SpeechClient()

response = client.recognize(config, audio)

In [ ]:
response

`response` is an object, autocomplete won't work on it, though. However, the output suggests that there is a `results` attribute.

**Exercise:** Get the `results` attribute of `response`.

In [ ]:
# YOUR CODE, ~1 line
None
# END OF YOR CODE

To fully unravel this nested object, we need syntax not yet properly discusses in this course, namely `[0]`. It indicates that we want the first (zero-th) result and the first (zero-th) alternative. This time, the API only gives on result and one alternative.

**Note:** The Google Speech Recognition API returns more results if we gave it more audio clips to translate at once, and more alternatives if it is not too sure about what was said, and came up with more options. Confidence is a number between `0` and `1` to indicate how ... confident Google is about its answer.

This is how we unravel `response` to the transcript text.

In [ ]:
response.results[0].alternatives[0].transcript

You have seen how to use existing software, to do a reasoanbly complicated task. Possibly you have never programmed before, yet using stuff from others allowed you to translate audio into text, without knowing how this was done. The artificial intelligence behind this translation was black-boxed, and is a field on its own.

**Take home**

 * Using existing software, for example on PyPI or github, can help you get something done;
 * You need to figure out how to tie together different software into something that gets your job done.
 * Using software from others has benefits:
  - if you write it yourself, you will do things wrong and have bugs messing up your system from time to time. Others may have more time for their specific problem and solve those with updates
  - it enforces you to write modular code, since you are not allowed to change the library. This often results in better maintainable code.
  - friends that will work on your code can read the documentation of the libraries you used, and get an idea of what is going on. Imagine all the work of explaining or documenting it yourself!
  - you can, if you really need to, change code of libraries, but it is something you should try to avoid.
  <br>
  **NEVER (NEVER!!) DO THIS VIA THE `site-packages` (OR `dist-packages`) DIRECTORIES OF THE PYTHON PATH.
  <br>
  Those files are deleted and replaced each update**
 * a lot is already out there!
 * not everything, though :(